# This program is an example. By applying this program, you can cross-validate search using RandomizedSearchCV for other process variables as well as time constants of second order process.

In [1]:
# ProcessIdentification class
# Necessary libraries
import numpy as np
import os
import tensorflow as tf
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.base import BaseEstimator, RegressorMixin
from sklearn.exceptions import NotFittedError
from datetime import datetime
he_init = tf.variance_scaling_initializer()

class SecondOrderProcessIdentification(BaseEstimator, RegressorMixin):
    def __init__(self, n_hidden_layers=2, n_neurons=100, optimizer_class=tf.train.MomentumOptimizer,
                 momentum = 0.9, learning_rate=0.01, n_inputs = 7, n_outputs = 1, batch_size=50, activation=tf.nn.relu,
                 initializer = None, learning_object=None, loaded_data=None, random_state=None):
        self.n_hidden_layers = n_hidden_layers
        self.n_neurons = n_neurons
        self.optimizer_class = optimizer_class
        self.momentum = momentum
        self.n_inputs = n_inputs
        self.n_outputs = n_outputs
        self.learning_rate = learning_rate
        self.batch_size = batch_size
        self.activation = activation
        self.initializer = initializer        
        self.learning_object = learning_object
        self.loaded_data = loaded_data
        self.random_state = random_state
        self._session = None
        
    def data_preparation(self):
        train_set, test_set = train_test_split(self.loaded_data, test_size=0.2, random_state=42)
        X_train, y_train = train_set.iloc[:,:7].values, train_set.iloc[:,7:].values
        X_test, y_test = test_set.iloc[:,:7].values, test_set.iloc[:,7:].values
        X_valid, X_train = X_train[:5000], X_train[5000:]
        y_valid, y_train = y_train[:5000], y_train[5000:]
        X_scale_minmax = X_train
        scaler = MinMaxScaler()
        scaler.fit(X_train)
        X_train = scaler.transform(X_train)
        X_valid = scaler.transform(X_valid)
        X_test = scaler.transform(X_test)   
        return X_train, y_train, X_valid, y_valid, X_test, y_test, X_scale_minmax
    
    def operating_data_preparation(self, X_scale_minmax):
        X_op, y_op = self.loaded_data.iloc[:,:7].values, self.loaded_data.iloc[:,7:].values
        scaler = MinMaxScaler()
        scaler.fit(X_scale_minmax)
        X_op = scaler.transform(X_op)
        return X_op, y_op

    def _dnn(self, inputs):
        for layer in range(self.n_hidden_layers):
            inputs = tf.layers.dense(inputs, self.n_neurons, kernel_initializer=self.initializer,
                                     name="hidden%d" % (layer + 1))
            inputs = self.activation(inputs, name="hidden%d_out" % (layer + 1))
        return inputs
    
    def _build_graph(self, n_inputs, n_outputs):
        if self.random_state is not None:
            tf.set_random_seed(self.random_state)
            np.random.seed(self.random_state)
            
        X = tf.placeholder(tf.float32, shape=(None, n_inputs), name="X")
        y = tf.placeholder(tf.float32, shape=(None), name="y")
        
        dnn_outputs = self._dnn(X)
        
        y_predict = tf.layers.dense(dnn_outputs, n_outputs, name="outputs")
        
        RMSE = tf.sqrt(tf.losses.mean_squared_error(y, y_predict), name="loss")
        
        optimizer = self.optimizer_class(learning_rate=self.learning_rate, momentum=self.momentum, use_nesterov=True)
        training_op = optimizer.minimize(RMSE)
        
        accuracy = tf.reduce_mean(1-(abs(y_predict - y)/y), name="accuracy")
        
        init = tf.global_variables_initializer()
        saver = tf.train.Saver()
        
        self._X, self._y = X, y
        self._y_predict, self._loss = y_predict, RMSE
        self._training_op, self._accuracy = training_op, accuracy
        self._init, self._saver = init, saver

    def close_session(self):
        if self._session:
            self._session.close()

    def _get_model_params(self):
        with self._graph.as_default():
            gvars = tf.get_collection(tf.GraphKeys.GLOBAL_VARIABLES)
        return {gvar.op.name: value for gvar, value in zip(gvars, self._session.run(gvars))}

    def _restore_model_params(self, model_params):
        gvar_names = list(model_params.keys())
        assign_ops = {gvar_name: self._graph.get_operation_by_name(gvar_name + "/Assign")
                      for gvar_name in gvar_names}
        init_values = {gvar_name: assign_op.inputs[1] for gvar_name, assign_op in assign_ops.items()}
        feed_dict = {init_values[gvar_name]: model_params[gvar_name] for gvar_name in gvar_names}
        self._session.run(assign_ops, feed_dict=feed_dict)
        
    def fit(self, X, y, n_epochs=20, X_valid=None, y_valid=None):
        self.close_session()
        
        self._graph = tf.Graph()
        
        # for early stopping
        max_checks_without_progress = 20
        checks_without_progress = 0
        best_loss = np.infty
        best_params = None
        
        
        with self._graph.as_default():
            self._build_graph(self.n_inputs, self.n_outputs)        
        
        self._session = tf.Session(graph=self._graph)

        with self._session.as_default() as sess:
            self._init.run()
            for epoch in range(n_epochs):
                rnd_idx = np.random.permutation(len(X))
                for rnd_indices in np.array_split(rnd_idx, len(X) // self.batch_size):
                    X_batch, y_batch = X[rnd_indices], y[rnd_indices]
                    feed_dict = {self._X: X_batch, self._y: y_batch}
                    sess.run(self._training_op, feed_dict=feed_dict)                    
                if X_valid is not None and y_valid is not None:
                    loss_val, acc_val = sess.run([self._loss, self._accuracy],
                                                 feed_dict={self._X: X_valid,
                                                            self._y: y_valid})
                    if loss_val < best_loss:
                        best_params = self._get_model_params()
                        best_loss = loss_val
                        checks_without_progress = 0
                    else:
                        checks_without_progress += 1
                    print("{}\tvalidation set loss: {:.6f}\tbest loss: {:.6f}\taccuracy: {:.2f}".format(
                        epoch, loss_val, best_loss, acc_val))
                    if checks_without_progress > max_checks_without_progress:
                        print("early stopping!")
                        break
                else:
                    loss_train, acc_train = sess.run([self._loss, self._accuracy],
                                                     feed_dict={self._X: X_batch,
                                                                self._y: y_batch})
                    print("{}\tlast training batch loss: {:.6f}\tAccuracy: {:.2f}".format(
                        epoch, loss_train, acc_train))
            # If you use an early stopping, you revert to the best model you've ever
            if best_params:
                self._restore_model_params(best_params)
            return self
    
    def predict(self, X, learning_object=None):
        if not self._session:
            raise NotFittedError("%s Object hasn't been trained yet" % self.__class__.__name__)
        with self._session.as_default() as sess:
            y_pred = self._y_predict.eval(feed_dict={self._X: X})

        return y_pred

    def save(self, path):
        self._saver.save(self._session, path)

C:\Users\user\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
learning_2nd = pd.read_excel('DataSecond_rand_limit_none_extra.xlsx')
pro_iden = SecondOrderProcessIdentification(loaded_data=learning_2nd)
X_train, y_train, X_valid, y_valid, X_test, y_test, X_scale_minmax = pro_iden.data_preparation()
y_train_TC, y_train_DC, y_train_TD = y_train[:,0:1], y_train[:,1:2], y_train[:,2:3]
y_valid_TC, y_valid_DC, y_valid_TD = y_valid[:,0:1], y_valid[:,1:2], y_valid[:,2:3]
y_test_TC, y_test_DC, y_test_TD = y_test[:,0:1], y_test[:,1:2], y_test[:,2:3]

In [3]:
from sklearn.model_selection import RandomizedSearchCV

param_distribs = {
    "n_neurons": [50, 70, 90, 100, 120, 140],
    "batch_size": [10, 50, 100, 150],
    "learning_rate": [0.00001, 0.00005, 0.0001, 0.00015, 0.0002],
    "n_hidden_layers": [2, 3, 4, 5],
    "momentum": [0.9, 0.99, 0.999]
}

rnd_search = RandomizedSearchCV(SecondOrderProcessIdentification(learning_object="tau", random_state=42),
                                param_distribs, n_iter=100, random_state=42, verbose=2)
fit_params={"X_valid": X_valid, "y_valid": y_valid_TC, "n_epochs": 1000}
rnd_search.fit(X_train, y_train_TC, **fit_params)

Fitting 3 folds for each of 100 candidates, totalling 300 fits
[CV] n_neurons=50, n_hidden_layers=2, momentum=0.99, learning_rate=0.0001, batch_size=10 
0	검증 세트 손실: 0.571487	최선의 손실: 0.571487	정확도: 0.96
1	검증 세트 손실: 0.373129	최선의 손실: 0.373129	정확도: 0.98
2	검증 세트 손실: 0.322104	최선의 손실: 0.322104	정확도: 0.98
3	검증 세트 손실: 0.347342	최선의 손실: 0.322104	정확도: 0.98
4	검증 세트 손실: 0.281356	최선의 손실: 0.281356	정확도: 0.98
5	검증 세트 손실: 0.272629	최선의 손실: 0.272629	정확도: 0.98
6	검증 세트 손실: 0.214457	최선의 손실: 0.214457	정확도: 0.99
7	검증 세트 손실: 0.211873	최선의 손실: 0.211873	정확도: 0.98
8	검증 세트 손실: 0.244651	최선의 손실: 0.211873	정확도: 0.98
9	검증 세트 손실: 0.280202	최선의 손실: 0.211873	정확도: 0.98
10	검증 세트 손실: 0.191852	최선의 손실: 0.191852	정확도: 0.99
11	검증 세트 손실: 0.216950	최선의 손실: 0.191852	정확도: 0.99
12	검증 세트 손실: 0.208394	최선의 손실: 0.191852	정확도: 0.99
13	검증 세트 손실: 0.224544	최선의 손실: 0.191852	정확도: 0.99
14	검증 세트 손실: 0.192365	최선의 손실: 0.191852	정확도: 0.99
15	검증 세트 손실: 0.208756	최선의 손실: 0.191852	정확도: 0.98
16	검증 세트 손실: 0.209884	최선의 손실: 0.191852	정확도: 0.99
17	검증 세트 손실: 0.238133	최선

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:  3.9min remaining:    0.0s


0	검증 세트 손실: 0.537399	최선의 손실: 0.537399	정확도: 0.96
1	검증 세트 손실: 0.425525	최선의 손실: 0.425525	정확도: 0.97
2	검증 세트 손실: 0.364596	최선의 손실: 0.364596	정확도: 0.98
3	검증 세트 손실: 0.392980	최선의 손실: 0.364596	정확도: 0.98
4	검증 세트 손실: 0.259876	최선의 손실: 0.259876	정확도: 0.98
5	검증 세트 손실: 0.241603	최선의 손실: 0.241603	정확도: 0.99
6	검증 세트 손실: 0.201294	최선의 손실: 0.201294	정확도: 0.99
7	검증 세트 손실: 0.228874	최선의 손실: 0.201294	정확도: 0.99
8	검증 세트 손실: 0.215601	최선의 손실: 0.201294	정확도: 0.99
9	검증 세트 손실: 0.240468	최선의 손실: 0.201294	정확도: 0.98
10	검증 세트 손실: 0.253763	최선의 손실: 0.201294	정확도: 0.99
11	검증 세트 손실: 0.184733	최선의 손실: 0.184733	정확도: 0.99
12	검증 세트 손실: 0.217218	최선의 손실: 0.184733	정확도: 0.99
13	검증 세트 손실: 0.208449	최선의 손실: 0.184733	정확도: 0.99
14	검증 세트 손실: 0.197117	최선의 손실: 0.184733	정확도: 0.99
15	검증 세트 손실: 0.209675	최선의 손실: 0.184733	정확도: 0.99
16	검증 세트 손실: 0.255327	최선의 손실: 0.184733	정확도: 0.99
17	검증 세트 손실: 0.177537	최선의 손실: 0.177537	정확도: 0.99
18	검증 세트 손실: 0.179123	최선의 손실: 0.177537	정확도: 0.99
19	검증 세트 손실: 0.269274	최선의 손실: 0.177537	정확도: 0.97
20	검증 세트 손실: 0.213122	최선의 손실: 

83	검증 세트 손실: 0.132606	최선의 손실: 0.117474	정확도: 0.99
84	검증 세트 손실: 0.166975	최선의 손실: 0.117474	정확도: 0.99
85	검증 세트 손실: 0.129789	최선의 손실: 0.117474	정확도: 0.99
86	검증 세트 손실: 0.240309	최선의 손실: 0.117474	정확도: 0.98
87	검증 세트 손실: 0.128242	최선의 손실: 0.117474	정확도: 0.99
88	검증 세트 손실: 0.130683	최선의 손실: 0.117474	정확도: 0.99
89	검증 세트 손실: 0.179780	최선의 손실: 0.117474	정확도: 0.99
90	검증 세트 손실: 0.123287	최선의 손실: 0.117474	정확도: 0.99
91	검증 세트 손실: 0.157103	최선의 손실: 0.117474	정확도: 0.99
92	검증 세트 손실: 0.132635	최선의 손실: 0.117474	정확도: 0.99
93	검증 세트 손실: 0.125936	최선의 손실: 0.117474	정확도: 0.99
94	검증 세트 손실: 0.134325	최선의 손실: 0.117474	정확도: 0.99
95	검증 세트 손실: 0.127654	최선의 손실: 0.117474	정확도: 1.00
96	검증 세트 손실: 0.132409	최선의 손실: 0.117474	정확도: 0.99
97	검증 세트 손실: 0.122295	최선의 손실: 0.117474	정확도: 0.99
98	검증 세트 손실: 0.145651	최선의 손실: 0.117474	정확도: 0.99
99	검증 세트 손실: 0.173398	최선의 손실: 0.117474	정확도: 0.99
100	검증 세트 손실: 0.144608	최선의 손실: 0.117474	정확도: 0.99
조기 종료!
[CV]  n_neurons=50, n_hidden_layers=2, momentum=0.99, learning_rate=0.0001, batch_size=10, total= 4.4min
[CV] 

60	검증 세트 손실: 0.113086	최선의 손실: 0.113086	정확도: 0.99
61	검증 세트 손실: 0.128275	최선의 손실: 0.113086	정확도: 0.99
62	검증 세트 손실: 0.128919	최선의 손실: 0.113086	정확도: 0.99
63	검증 세트 손실: 0.144978	최선의 손실: 0.113086	정확도: 0.99
64	검증 세트 손실: 0.110684	최선의 손실: 0.110684	정확도: 1.00
65	검증 세트 손실: 0.146820	최선의 손실: 0.110684	정확도: 0.99
66	검증 세트 손실: 0.120581	최선의 손실: 0.110684	정확도: 0.99
67	검증 세트 손실: 0.161544	최선의 손실: 0.110684	정확도: 0.99
68	검증 세트 손실: 0.136063	최선의 손실: 0.110684	정확도: 0.99
69	검증 세트 손실: 0.151838	최선의 손실: 0.110684	정확도: 0.99
70	검증 세트 손실: 0.122848	최선의 손실: 0.110684	정확도: 0.99
71	검증 세트 손실: 0.120826	최선의 손실: 0.110684	정확도: 0.99
72	검증 세트 손실: 0.155346	최선의 손실: 0.110684	정확도: 0.99
73	검증 세트 손실: 0.120259	최선의 손실: 0.110684	정확도: 0.99
74	검증 세트 손실: 0.154917	최선의 손실: 0.110684	정확도: 0.99
75	검증 세트 손실: 0.112707	최선의 손실: 0.110684	정확도: 0.99
76	검증 세트 손실: 0.122605	최선의 손실: 0.110684	정확도: 0.99
77	검증 세트 손실: 0.139462	최선의 손실: 0.110684	정확도: 0.99
78	검증 세트 손실: 0.161110	최선의 손실: 0.110684	정확도: 0.99
79	검증 세트 손실: 0.143786	최선의 손실: 0.110684	정확도: 0.99
80	검증 세트 손실: 0.12726

...

4	검증 세트 손실: 0.793201	최선의 손실: 0.793201	정확도: 0.94
5	검증 세트 손실: 0.510002	최선의 손실: 0.510002	정확도: 0.96
6	검증 세트 손실: 0.396616	최선의 손실: 0.396616	정확도: 0.97
7	검증 세트 손실: 0.341218	최선의 손실: 0.341218	정확도: 0.98
8	검증 세트 손실: 0.347590	최선의 손실: 0.341218	정확도: 0.98
9	검증 세트 손실: 0.353077	최선의 손실: 0.341218	정확도: 0.98
10	검증 세트 손실: 0.309453	최선의 손실: 0.309453	정확도: 0.98
11	검증 세트 손실: 0.272352	최선의 손실: 0.272352	정확도: 0.98
12	검증 세트 손실: 0.243200	최선의 손실: 0.243200	정확도: 0.98
13	검증 세트 손실: 0.296574	최선의 손실: 0.243200	정확도: 0.98
14	검증 세트 손실: 0.306004	최선의 손실: 0.243200	정확도: 0.98
15	검증 세트 손실: 0.296801	최선의 손실: 0.243200	정확도: 0.98
16	검증 세트 손실: 0.297787	최선의 손실: 0.243200	정확도: 0.98
17	검증 세트 손실: 0.286028	최선의 손실: 0.243200	정확도: 0.98
18	검증 세트 손실: 0.307155	최선의 손실: 0.243200	정확도: 0.98
19	검증 세트 손실: 0.302029	최선의 손실: 0.243200	정확도: 0.97
20	검증 세트 손실: 0.300033	최선의 손실: 0.243200	정확도: 0.98
21	검증 세트 손실: 0.239468	최선의 손실: 0.239468	정확도: 0.98
22	검증 세트 손실: 0.244850	최선의 손실: 0.239468	정확도: 0.98
23	검증 세트 손실: 0.273421	최선의 손실: 0.239468	정확도: 0.98
24	검증 세트 손실: 0.237279	최선의 

57	검증 세트 손실: 0.159363	최선의 손실: 0.120759	정확도: 0.99
58	검증 세트 손실: 0.151110	최선의 손실: 0.120759	정확도: 0.99
59	검증 세트 손실: 0.137331	최선의 손실: 0.120759	정확도: 0.99
60	검증 세트 손실: 0.151837	최선의 손실: 0.120759	정확도: 0.99
61	검증 세트 손실: 0.166600	최선의 손실: 0.120759	정확도: 0.99
62	검증 세트 손실: 0.149460	최선의 손실: 0.120759	정확도: 0.99
63	검증 세트 손실: 0.147485	최선의 손실: 0.120759	정확도: 0.99
64	검증 세트 손실: 0.165996	최선의 손실: 0.120759	정확도: 0.99
65	검증 세트 손실: 0.166731	최선의 손실: 0.120759	정확도: 0.99
66	검증 세트 손실: 0.178745	최선의 손실: 0.120759	정확도: 0.99
67	검증 세트 손실: 0.134567	최선의 손실: 0.120759	정확도: 0.99
68	검증 세트 손실: 0.125005	최선의 손실: 0.120759	정확도: 0.99
69	검증 세트 손실: 0.181546	최선의 손실: 0.120759	정확도: 0.99
70	검증 세트 손실: 0.188126	최선의 손실: 0.120759	정확도: 0.99
71	검증 세트 손실: 0.155541	최선의 손실: 0.120759	정확도: 0.99
72	검증 세트 손실: 0.182614	최선의 손실: 0.120759	정확도: 0.98
73	검증 세트 손실: 0.167905	최선의 손실: 0.120759	정확도: 0.99
74	검증 세트 손실: 0.164753	최선의 손실: 0.120759	정확도: 0.99
75	검증 세트 손실: 0.163634	최선의 손실: 0.120759	정확도: 0.99
76	검증 세트 손실: 0.137351	최선의 손실: 0.120759	정확도: 0.99
77	검증 세트 손실: 0.24960

[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed: 1178.2min finished


0	검증 세트 손실: 15.291970	최선의 손실: 15.291970	정확도: -0.31
1	검증 세트 손실: 9.316240	최선의 손실: 9.316240	정확도: 0.12
2	검증 세트 손실: 4.930637	최선의 손실: 4.930637	정확도: 0.67
3	검증 세트 손실: 2.682984	최선의 손실: 2.682984	정확도: 0.88
4	검증 세트 손실: 1.148273	최선의 손실: 1.148273	정확도: 0.92
5	검증 세트 손실: 0.523348	최선의 손실: 0.523348	정확도: 0.97
6	검증 세트 손실: 0.378598	최선의 손실: 0.378598	정확도: 0.98
7	검증 세트 손실: 0.312399	최선의 손실: 0.312399	정확도: 0.98
8	검증 세트 손실: 0.260060	최선의 손실: 0.260060	정확도: 0.98
9	검증 세트 손실: 0.217714	최선의 손실: 0.217714	정확도: 0.99
10	검증 세트 손실: 0.189885	최선의 손실: 0.189885	정확도: 0.98
11	검증 세트 손실: 0.190363	최선의 손실: 0.189885	정확도: 0.98
12	검증 세트 손실: 0.158574	최선의 손실: 0.158574	정확도: 0.99
13	검증 세트 손실: 0.158264	최선의 손실: 0.158264	정확도: 0.99
14	검증 세트 손실: 0.141534	최선의 손실: 0.141534	정확도: 0.99
15	검증 세트 손실: 0.139620	최선의 손실: 0.139620	정확도: 0.99
16	검증 세트 손실: 0.152428	최선의 손실: 0.139620	정확도: 0.99
17	검증 세트 손실: 0.142442	최선의 손실: 0.139620	정확도: 0.99
18	검증 세트 손실: 0.133611	최선의 손실: 0.133611	정확도: 0.99
19	검증 세트 손실: 0.138056	최선의 손실: 0.133611	정확도: 0.99
20	검증 세트 손실: 0.125788	최선의 손

RandomizedSearchCV(cv=None, error_score='raise',
          estimator=SecondOrderProcessIdentification(activation=<function relu at 0x00000240E06DCBF8>,
                 batch_size=50, initializer=None, learning_object='tau',
                 learning_rate=0.01, loaded_data=None, momentum=0.9,
                 n_hidden_layers=2, n_inputs=7, n_neurons=100, n_outputs=1,
                 optimizer_class=<class 'tensorflow.python.training.momentum.MomentumOptimizer'>,
                 random_state=42),
          fit_params=None, iid=True, n_iter=100, n_jobs=1,
          param_distributions={'n_neurons': [50, 70, 90, 100, 120, 140], 'batch_size': [10, 50, 100, 150], 'learning_rate': [1e-05, 5e-05, 0.0001, 0.00015, 0.0002], 'n_hidden_layers': [2, 3, 4, 5], 'momentum': [0.9, 0.99, 0.999]},
          pre_dispatch='2*n_jobs', random_state=42, refit=True,
          return_train_score='warn', scoring=None, verbose=2)

In [4]:
rnd_search.best_params_

{'n_neurons': 100,
 'n_hidden_layers': 4,
 'momentum': 0.999,
 'learning_rate': 1e-05,
 'batch_size': 50}

In [5]:
from sklearn.metrics import mean_squared_error

y_pred = rnd_search.predict(X_test)
mean_squared_error(y_test_TC, y_pred)

0.00984315956077307